<!-- The "view-in-github" magic section ID is handled specially by Colab, which will not show its contents. Note that this only seems to work if this is the first section. -->
**You are viewing the source version of the Loudspeaker Explorer notebook.** You can also open the ready-to-use, published version in [Colab]((https://colab.research.google.com/github/dechamps/LoudspeakerExplorer-rendered/blob/master/Loudspeaker_Explorer.ipynb)).

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/dechamps/LoudspeakerExplorer-rendered/blob/master/Loudspeaker_Explorer.ipynb)


# The Loudspeaker Explorer

_By [Etienne Dechamps](https://www.audiosciencereview.com/forum/index.php?members/edechamps.4453/) (etienne@edechamps.fr)_ - [ASR thread](https://www.audiosciencereview.com/forum/index.php?threads/loudspeaker-explorer-analyze-visualize-compare-speaker-data.11503/) - [GitHub](https://github.com/dechamps/LoudspeakerExplorer) - _[Changelog](https://github.com/dechamps/LoudspeakerExplorer/commits/c99c6e7ffb1817fa8611bbb0b2cead80b0fc28a2) (built from [c99c6e7](https://github.com/dechamps/LoudspeakerExplorer/commit/c99c6e7ffb1817fa8611bbb0b2cead80b0fc28a2) on [2020-03-20T09:29:55Z](https://github.com/dechamps/LoudspeakerExplorer/actions/runs/59547117))_

**All data provided by [amirm](https://www.audiosciencereview.com/forum/index.php?members/amirm.2/) from [AudioScienceReview](https://www.audiosciencereview.com/). Consider [making a donation](https://www.audiosciencereview.com/forum/index.php?threads/how-to-support-audio-science-review.8150/) if you enjoy the use of this data.**

Welcome to the [Loudspeaker Explorer](https://colab.research.google.com/github/dechamps/LoudspeakerExplorer-rendered/blob/master/Loudspeaker_Explorer.ipynb), a speaker measurement visualization, analysis and comparison tool. This is an interactive [Colaboratory Notebook](https://colab.research.google.com/).

## How to use this notebook

To run the code and (re)generate the data, go to the **Runtime** menu and click **Run all** (CTRL+F9). **You will need to repeat this every time you change any of the settings or code** (e.g. if you enable or disable speakers).

**All the charts are interactive.** Use the mousewheel to zoom, and drag & drop to pan. Click on a legend entry to highlight a single response; hold shift to highlight multiple responses. Double-click to reset the view.

**Charts can take a few seconds to load when scrolling**, especially if you're using the notebook for the first time. Be patient.

**Charts will not be generated if the section they're under is folded while the notebook is running.** To manually load a chart after running the notebook, click on the square to the left of the *Show Code* button. Or simply use *Run all* again after unfolding the section.

## Acknowledgments

None of this would have been possible without [amirm](https://www.audiosciencereview.com/forum/index.php?members/amirm.2/)'s [tremendous work](https://www.audiosciencereview.com/forum/index.php?threads/announcement-asr-will-be-measuring-speakers.10725/) in measuring speakers. All the data used by this tool is from measurements made by amirm for [AudioScienceReview](https://www.audiosciencereview.com/). If you like what you see, [consider making a donation](https://www.audiosciencereview.com/forum/index.php?threads/how-to-support-audio-science-review.8150/).

This notebook is powered by amazing software: [Google Colaboratory](https://colab.research.google.com/), [Jupyter](https://jupyter.org/), [Jupytext](https://github.com/mwouts/jupytext), [Pandas](https://pandas.pydata.org/), and [Altair](https://altair-viz.github.io/).

## License

The *code* and accompanying text of Loudspeaker Explorer is published under [MIT License](https://github.com/dechamps/LoudspeakerExplorer/blob/master/LICENSE.txt).

The *measurement data* is not part of Loudspeaker Explorer - it is published by Audio Science Review LLC under the [Creative Commons BY-NC-SA 4.0 license](https://creativecommons.org/licenses/by-nc-sa/4.0/). Because this is a "share alike" license, **all data generated by Loudspeaker Explorer, including the charts, is de facto licensed under these terms as well**. Note that these license terms do not apply to measurements published before 2020-03-02, as these do not come with a clear license.

## Other tools

You might also be interested in:

 - [pozz](https://www.audiosciencereview.com/forum/index.php?members/pozz.7752/)'s [ASR Speaker Review and Measurement Index](https://www.audiosciencereview.com/forum/index.php?pages/SpeakerTestData/)
 - [MZKM](https://www.audiosciencereview.com/forum/index.php?members/mzkm.4645/)'s [Preference Rating data](https://docs.google.com/spreadsheets/d/e/2PACX-1vRVN63daR6Ph8lxhCDUEHxWq_gwV0wEjL2Q1KRDA0J4i_eE1JS-JQYSZy7kCQZMKtRnjTOn578fYZPJ/pubhtml)
 - [pierre](https://www.audiosciencereview.com/forum/index.php?members/pierre.344/)'s [Spinorama visualizations](https://pierreaubert.github.io/spinorama/)

# Preliminary boilerplate

In [1]:
#@markdown
# https://jakevdp.github.io/blog/2017/12/05/installing-python-packages-from-jupyter/
import sys
!{sys.executable} -m pip install --progress-bar=off numpy pandas engarde yattag altair

from pathlib import Path
import re
import numpy as np
import pandas as pd
import engarde.decorators as ed
import IPython
import yattag
import altair as alt

    Running setup.py install for yattag ... -

 done


    Running setup.py install for toolz ... -

 done


/opt/hostedtoolcache/Python/3.8.2/x64/lib/python3.8/site-packages/engarde/checks.py:13: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


# Speaker selection

This is the most important setting. Here you can select the speakers you wish to analyze and compare. See below for more information on each speaker. **Don't forget to click "Runtime" → "Run all" after changing your selection.**

Note that the following speakers, despite having been measured by amirm, are not (yet) available in this tool:

 - [**Genelec 8341A (before treble ripple issue fix)**](https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/page-2#post-335133): the raw data was [not published](https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/page-5#post-335291). The data shown here is from the [fixed](https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/#post-335109) [measurement](https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/).
 - [**Kali IN-8 (damaged sample)**](https://www.audiosciencereview.com/forum/index.php?threads/kali-audio-in-8-studio-monitor-review.10897/): the raw data was not published. The data shown here is for the [good sample](https://www.audiosciencereview.com/forum/index.php?threads/kali-audio-in-8-studio-monitor-review.10897/page-29#post-318617).
 - [**Neumann KH80 (sample 2, low order)**](https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/): the raw data was not published. The data shown here is from the [high order measurement](https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/page-12#post-324456).
 - [**NHT Pro M-00**](https://www.audiosciencereview.com/forum/index.php?threads/nht-pro-m-00-powered-monitor-review.10859/): the raw data was not published.
 - [**Yamaha HS5**](https://www.audiosciencereview.com/forum/index.php?threads/yamaha-hs5-powered-monitor-review.10967/): the raw data published is incomplete and does not come in the standard zipfile format that the tool expects.

Also note that the datasets for **JBL 305P MkII** and **Neumann KH80 (sample 1)** are missing *Directivity Index* data. Due to a bug in the tool this also breaks the Spinorama charts unless another speaker is also selected.

Also note that a [measurement artefact](https://www.audiosciencereview.com/forum/index.php?threads/klipsch-r-41m-bookshelf-speaker-review.11566/page-3#post-332136) in the form of a slight [ripple in high frequencies](https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/page-10#post-324189) (above 4 kHz or so) is present in all measurements made before 2020-02-23. This was [fixed](https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/#post-335109) starting from the Genelec 8341A measurement.

**How to add a new speaker**: in the following code block, add a new variable, and repeat the pattern in the `speakers` variable assignment. That's it - everything else should take care of itself. Note that the tool expects a zipfile in the format that amirm publishes (which presumably is the Klippel analysis software export format). If you want to upload the zipfile manually instead of using `Data URL`, you can do that using the Colab file browser on the left - just make sure the name of the file matches the `Speaker` field in the raw specification so that the tool can find it.

In [2]:
#@markdown
speaker_enable_AdamAudio_S2V = False  # @param {type:"boolean"}
speaker_enable_AscendAcoustics_CBM170SE = False  # @param {type:"boolean"}
speaker_enable_AscendAcoustics_CMT340SECenter = False  # @param {type:"boolean"}
speaker_enable_AscendAcoustics_Sierra2 = False  # @param {type:"boolean"}
speaker_enable_DaytonAudio_B652AIR = False  # @param {type:"boolean"}
speaker_enable_Elac_AdanteAS61 = False  # @param {type:"boolean"}
speaker_enable_Emotiva_Airmotiv6s = False  # @param {type:"boolean"}
speaker_enable_Genelec_8341A = False  # @param {type:"boolean"}
speaker_enable_Harbeth_Monitor30_LowOrder = False  # @param {type:"boolean"}
speaker_enable_Harbeth_Monitor30_HighOrder = False  # @param {type:"boolean"}
speaker_enable_JBL_305PMkII = False  # @param {type:"boolean"}
speaker_enable_JBL_705P_Sample1 = False  # @param {type:"boolean"}
speaker_enable_JBL_705P_Sample2 = False  # @param {type:"boolean"}
speaker_enable_JBL_Control1Pro = False  # @param {type:"boolean"}
speaker_enable_JBL_OneSeries104 = False  # @param {type:"boolean"}
speaker_enable_Kali_IN8 = False  # @param {type:"boolean"}
speaker_enable_KEF_LS50 = False  # @param {type:"boolean"}
speaker_enable_KEF_Q100 = False  # @param {type:"boolean"}
speaker_enable_KEF_R3 = False  # @param {type:"boolean"}
speaker_enable_Klipsch_R41M = False  # @param {type:"boolean"}
speaker_enable_Klipsch_RP600M = True  # @param {type:"boolean"}
speaker_enable_Micca_RB42 = False  # @param {type:"boolean"}
speaker_enable_Neumann_KH80_Sample1 = False  # @param {type:"boolean"}
speaker_enable_Neumann_KH80_Sample2 = False  # @param {type:"boolean"}
speaker_enable_Pioneer_SPBS22LR = False  # @param {type:"boolean"}
speaker_enable_Polk_T15 = False  # @param {type:"boolean"}
speaker_enable_Realistic_MC1000 = False  # @param {type:"boolean"}
speaker_enable_Revel_C52 = False  # @param {type:"boolean"}
speaker_enable_Revel_F35 = True  # @param {type:"boolean"}
speaker_enable_Revel_M16 = False  # @param {type:"boolean"}
speaker_enable_SelahAudio_RC3R = False  # @param {type:"boolean"}
speaker_enable_Tannoy_System600 = False  # @param {type:"boolean"}
speaker_enable_ZaphAudio_ZA52TM_Winkleswizard = True  # @param {type:"boolean"}

speakers = pd.DataFrame([{
    'Speaker': 'Adam Audio S2V',
    'Enabled': speaker_enable_AdamAudio_S2V,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/adam-s2v-spinorama-cea2034-zip.50119/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/adam-s2v-studio-monitor-review.11455/',
    'Product URL': 'https://www.adam-audio.com/en/s-series/s2v/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/adam-s2v-monitor-powered-studio-speaker-audio-review-jpg.50100/',
    'Measurement Date': pd.Timestamp('2020-02-14'),
    'Active': True,
    'Price (Single, USD)': 875.00,
  }, {
    'Speaker': 'Ascend Acoustics CBM-170 SE',
    'Enabled': speaker_enable_AscendAcoustics_CBM170SE,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-cbm170-spinorama-data-zip.52802/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/ascend-cbm-170-se-speaker-review.11839/',
    'Product URL': 'http://www.ascendacoustics.com/pages/products/speakers/cbm170/cbm170.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-acoustics-cbm-170-bookshelf-speaker-audio-review-jpg.52606/',
    'Measurement Date': pd.Timestamp('2020-03-02'),
    'Active': False,
    'Price (Single, USD)': 150.00,
  }, {
    'Speaker': 'Ascend Acoustics CMT-340 SE Center',
    'Enabled': speaker_enable_AscendAcoustics_CMT340SECenter,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-acoustics-cmt-340-spin-data-zip.52403/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/ascend-cmt-340-se-center-channel-speaker-review.11797/',
    'Product URL': 'http://www.ascendacoustics.com/pages/products/speakers/cmt340c/cmt340c.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-acoustics-cmt-340-se-center-home-theater-speaker-baloon-audio-review-jpg.52239/',
    'Measurement Date': pd.Timestamp('2020-02-29'),
    'Active': False,
    'Price (Single, USD)': 150.00,
  }, {
    'Speaker': 'Ascend Acoustics Sierra-2',
    'Enabled': speaker_enable_AscendAcoustics_Sierra2,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-sierra-2-spin-data-zip.52401/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/ascend-sierra-2-speaker-review.11813/',
    'Product URL': 'http://www.ascendacoustics.com/pages/products/speakers/SRM2/srm2.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/ascend-acoustics-sierra-2-bookshelf-stand-mount-speaker-audio-review-jpg.52386/',
    'Measurement Date': pd.Timestamp('2020-03-01'),
    'Active': False,
    'Price (Single, USD)': 740.00,
  }, {
    'Speaker': 'Dayton Audio B652-AIR',
    'Enabled': speaker_enable_DaytonAudio_B652AIR,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/dayton-audio-b652-air-spinorama-zip.49763/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/dayton-audio-b652-air-speaker-review.11410/',
    'Product URL': 'https://www.daytonaudio.com/product/1243/b652-air-6-1-2-2-way-bookshelf-speaker-with-amt-tweeter-pair',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/dayton-audio-b652-air-bookshelf-cheap-speakers-audio-review-jpg.49739/',
    'Measurement Date': pd.Timestamp('2020-02-11'),
    'Active': False,
    'Price (Single, USD)': 39.00,
  }, {
    'Speaker': 'Elac Adante AS-61',
    'Enabled': speaker_enable_Elac_AdanteAS61,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/elac-adante-as-61-cea-2034-spin-data-zip.50439/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/elac-adante-as-61-speaker-review.11507/',
    'Product URL': 'https://www.elac.com/series/adante/as-61/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/elac-adante-as-61-bookshelf-speaker-audio-review-jpg.50415/',
    'Measurement Date': pd.Timestamp('2020-02-16'),
    'Active': False,
    'Price (Single, USD)': 1250.00,
  }, {
    'Speaker': 'Emotiva Airmotiv 6s',
    'Enabled': speaker_enable_Emotiva_Airmotiv6s,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/emotiva-airmotive-6s-spinorama-zip.48091/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/emotiva-airmotiv-6s-powered-speaker-review.11185/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/emotiva-airmotive-6s-powered-monitor-speaker-review-jpg.48017/',
    'Measurement Date': pd.Timestamp('2020-01-31'),
    'Active': True,
    'Price (Single, USD)': 250.00,
  }, {
    'Speaker': 'Genelec 8341A',
    'Enabled': speaker_enable_Genelec_8341A,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/genelec-8431a-spl-adjusted-zip.51413/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/genelec-8341a-sam%E2%84%A2-studio-monitor-review.11652/',
    'Product URL': 'https://www.genelec.com/8341a',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/genelec-8341a-sam%E2%84%A2-studio-monitor-powered-speaker-audio-review-jpg.51396/',
    'Measurement Date': pd.Timestamp('2020-02-23'),
    'Active': True,
    'Price (Single, USD)': 2950.00,
  }, {
    'Speaker': 'Harbeth Monitor 30 (low order)',
    'Enabled': speaker_enable_Harbeth_Monitor30_LowOrder,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/harbeth-monitor-ces2034-spinorama-zip.47527/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/harbeth-monitor-30-speaker-review.11108/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/harbeth-monitor-30-speaker-review-jpg.47512/',
    'Measurement Date': pd.Timestamp('2020-01-26'),
    'Active': False,
    'Price (Single, USD)': 1600.00,
  }, {
    'Speaker': 'Harbeth Monitor 30 (high order)',
    'Enabled': speaker_enable_Harbeth_Monitor30_HighOrder,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/harbeth-30-high-order-spin-data-zip.49385/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/page-10#post-324345',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/harbeth-monitor-30-speaker-review-jpg.47512/',
    'Measurement Date': pd.Timestamp('2020-02-09'),
    'Active': False,
    'Price (Single, USD)': 1600.00,
  }, {
    'Speaker': 'JBL 305P MkII',
    'Enabled': speaker_enable_JBL_305PMkII,
    # https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-monitor-review.11018/page-2#post-310325
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-305p-mark-ii-cea2034-zip.46835/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/jbl-305p-mkii-and-control-1-pro-monitors-review.10811/',
    'Product URL': 'https://www.jbl.com/studio-monitors/305PMKII.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-305p-mkii-speaker-powered-monitor-review-jpg.45226/',
    'Measurement Date': pd.Timestamp('2020-01-10'),
    'Active': True,
    'Price (Single, USD)': 150.00,
  }, {
    'Speaker': 'JBL 705P (sample 1)',
    'Enabled': speaker_enable_JBL_705P_Sample1,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-705p-spinorama-zip.53447/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/jbl-705p-studio-monitor-review.11944/',
    'Product URL': 'https://jblpro.com/products/705p',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-705p-studio-powered-monitor-distortion-and-spl-speaker-review-jpg.53429/',
    'Measurement Date': pd.Timestamp('2020-03-09'),
    'Active': True,
    'Price (Single, USD)': 1000.00,
  }, {
    'Speaker': 'JBL 705P (sample 2)',
    'Enabled': speaker_enable_JBL_705P_Sample2,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-705p-sample-2-zip.53543/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/jbl-705p-studio-monitor-review.11944/page-8#post-346907',
    'Product URL': 'https://jblpro.com/products/705p',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-705p-studio-powered-monitor-distortion-and-spl-speaker-review-jpg.53429/',
    'Measurement Date': pd.Timestamp('2020-03-10'),
    'Active': True,
    'Price (Single, USD)': 1000.00,
  }, {
    'Speaker': 'JBL Control 1 Pro',
    'Enabled': speaker_enable_JBL_Control1Pro,
    # https://www.audiosciencereview.com/forum/index.php?threads/jbl-305p-mkii-and-control-1-pro-monitors-review.10811/page-24#post-315827
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-control-1-pro-zip.47821/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/jbl-305p-mkii-and-control-1-pro-monitors-review.10811/',
    'Product URL': 'https://jblpro.com/en/products/control-1-pro',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-control-1-pro-monitor-review-jpg.45228/',
    'Measurement Date': pd.Timestamp('2020-01-10'),
    'Active': True,
    'Price (Single, USD)': 82.00,
  }, {
    'Speaker': 'JBL One Series 104',
    'Enabled': speaker_enable_JBL_OneSeries104,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-104-spinorama-zip.47297/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/jbl-one-series-104-powered-monitor-review.11076/',
    'Product URL': 'https://jblpro.com/en-US/products/104',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/jbl-one-series-104-powered-monitor-speaker-review-jpg.47273/',
    'Measurement Date': pd.Timestamp('2020-01-25'),
    'Active': True,
    'Price (Single, USD)': 65.00,
  }, {
    'Speaker': 'Kali Audio IN-8',
    'Enabled': speaker_enable_Kali_IN8,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kali-in-8-spinorama-zip.48347/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/kali-audio-in-8-studio-monitor-review.10897/page-29#post-318617',
    'Product URL': 'https://www.kaliaudio.com/independence',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kali-audio-in-8-studio-monitor-powered-speaker-review-jpg.45827/',
    'Measurement Date': pd.Timestamp('2020-02-02'),
    'Active': True,
    'Price (Single, USD)': 400.00,
  }, {
    'Speaker': 'KEF LS50',
    'Enabled': speaker_enable_KEF_LS50,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-ls50-ces2034-zip.47785/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/kef-ls50-bookshelf-speaker-review.11144/',
    'Product URL': 'https://us.kef.com/catalog/product/view/id/1143/s/ls50-mini-monitor-speaker-pair/category/94/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-ls50-bookshelf-speaker-review-jpg.47768/',
    'Measurement Date': pd.Timestamp('2020-01-28'),
    'Active': False,
    'Price (Single, USD)': 750.00,
  }, {
    'Speaker': 'KEF Q100',
    'Enabled': speaker_enable_KEF_Q100,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-q100-spinorama-zip.53776/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/kef-q100-speaker-review.11987/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-q100-bookshelf-speaker-coaxial-driver-audio-review-jpg.53759/',
    'Measurement Date': pd.Timestamp('2020-03-11'),
    'Active': False,
    'Price (Single, USD)': 225.00,
  }, {
    'Speaker': 'KEF R3',
    'Enabled': speaker_enable_KEF_R3,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-r3-spinorama-zip.54005/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/kef-r3-speaker-review.12021/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/kef-r3-three-way-stand-mount-speaker-audio-review-jpg.53994/',
    'Measurement Date': pd.Timestamp('2020-03-12'),
    'Active': False,
    'Price (Single, USD)': 1000.00,
  }, {
    'Speaker': 'Klipsch R-41M',
    'Enabled': speaker_enable_Klipsch_R41M,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/klipsch-r41m-spin-data-zip.50860/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/klipsch-r-41m-bookshelf-speaker-review.11566/',
    'Product URL': 'https://www.klipsch.com/products/r-41m-bookshelf-speaker-blk-gnm',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/klipsch-r-41m-booksehlf-speaker-audio-review-jpg.50841/',
    'Measurement Date': pd.Timestamp('2020-02-19'),
    'Active': False,
    'Price (Single, USD)': 75.00,
  }, {
    'Speaker': 'Klipsch RP-600M',
    'Enabled': speaker_enable_Klipsch_RP600M,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/klipsch-rp-600m-spinorama-zip.55056/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/klipsch-rp-600m-speaker-review.12138/',
    'Product URL': 'https://www.klipsch.com/products/rp-600m-bookshelf-speaker',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/klipsch-rp-600m-bookshelf-speaker-audio-review-jpg.55039/',
    'Measurement Date': pd.Timestamp('2020-03-19'),
    'Active': False,
    'Price (Single, USD)': 315.00,
  }, {
    'Speaker': 'Micca RB42',
    'Enabled': speaker_enable_Micca_RB42,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/micca-rb42-cea2034-spinorama-zip.48638/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/micca-rb42-bookshelf-speaker-review.11267/',
    'Product URL': 'https://www.miccatron.com/micca-rb42-reference-bookshelf-speakers/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/micca-rb42-bookshelf-budget-speaker-review-jpg.48623/',
    'Measurement Date': pd.Timestamp('2020-02-04'),
    'Active': False,
    'Price (Single, USD)': 75.00,
  }, {
    'Speaker': 'Neumann KH 80 DSP (sample 1)',
    'Enabled': speaker_enable_Neumann_KH80_Sample1,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/neumann-kh-80-cea2034-zip.46824/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-monitor-review.11018/',
    'Product URL': 'https://www.neumann.com/homestudio/en/kh-80',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/neumann-kh-80-dsp-monitor-active-studio-pro-speaker-audio-review-jpg.46803/',
    'Measurement Date': pd.Timestamp('2020-01-21'),
    'Active': True,
    'Price (Single, USD)': 500.00,
  }, {
    'Speaker': 'Neumann KH 80 DSP (sample 2)',
    'Enabled': speaker_enable_Neumann_KH80_Sample2,
    # https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/page-12#post-324456
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/neumann-kh80-dsp-1000-point-order-20-spin-datra-zip.49443/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/neumann-kh-80-dsp-speaker-measurements-take-two.11323/',
    'Product URL': 'https://www.neumann.com/homestudio/en/kh-80',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/neumann-kh-80-dsp-monitor-active-studio-pro-speaker-audio-review-jpg.46803/',
    'Measurement Date': pd.Timestamp('2020-02-08'),
    'Active': True,
    'Price (Single, USD)': 500.00,
  }, {
    'Speaker': 'Pioneer SP-BS22-LR',
    'Enabled': speaker_enable_Pioneer_SPBS22LR,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/pioneer-sp-bs22-lr-spinorama-2-zip.49024/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/pioneer-sp-bs22-lr-bookshelf-speaker-review.11303/',
    'Product URL': 'https://intl.pioneer-audiovisual.com/products/speakers/sp-bs22-lr/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/pioneer-sp-bs22-lr-budget-bookshelf-speaker-review-jpg.48945/',
    'Measurement Date': pd.Timestamp('2020-02-07'),
    'Active': False,
    'Price (Single, USD)': 80.00,
  }, {
    'Speaker': 'Polk T15',
    'Enabled': speaker_enable_Polk_T15,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/polk-t15-spin-data-zip.52404/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/polk-t15-bookshelf-speaker-review.11720/',
    'Product URL': 'https://en.polkaudio.com/shop/polkaudio-tseries/t15',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/polk-t15-bookshelf-budget-speakers-audio-review-jpg.51865/',
    'Measurement Date': pd.Timestamp('2020-02-27'),
    'Active': False,
    'Price (Single, USD)': 40.00,
  }, {
    'Speaker': 'Realistic MC-1000',
    'Enabled': speaker_enable_Realistic_MC1000,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/realistic-mc-1000-spinorama-zip.48797/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/mc-1000-best-speaker-in-the-world.11283/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/realistic-mc-1000-radio-shack-2-way-vintage-speaker-listing-jpg.48786/',
    'Measurement Date': pd.Timestamp('2020-02-06'),
    'Active': False,
    'Price (Single, USD)': 120.00,  # $30 in 1978, adjusted for inflation
  }, {
    'Speaker': 'Revel C52',
    'Enabled': speaker_enable_Revel_C52,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-c52-spinorama-zip.52515/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/revel-c52-speaker-review-and-measurements.10934/',
    'Product URL': 'https://www.revelspeakers.com/support/legacy/lsupport-center-channel/C52-.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-c52-center-speaker-3-way-review-jpg.46189/',
    'Measurement Date': pd.Timestamp('2020-01-17'),
    'Active': False,
    'Price (Single, USD)': 2500.00,
  }, {
    'Speaker': 'Revel F35',
    'Enabled': speaker_enable_Revel_F35,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-f35-spinorama-zip.54290/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/revel-f35-speaker-review.12053/',
    'Product URL': 'https://www.revelspeakers.com/products/types/floorstanding/F35-.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-f35-speaker-audio-review-jpg.54271/',
    'Measurement Date': pd.Timestamp('2020-03-15'),
    'Active': False,
    'Price (Single, USD)': 800.00,
  }, {
    'Speaker': 'Revel M16',
    'Enabled': speaker_enable_Revel_M16,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-m16-spin-zip.52914/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/revel-m16-speaker-review.11884/',
    'Product URL': 'https://www.revelspeakers.com/products/types/bookshelf/M16-.html',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/revel-m16-standmount-bookshelf-high-end-speaker-audio-review-jpg.52897/',
    'Measurement Date': pd.Timestamp('2020-03-05'),
    'Active': False,
    'Price (Single, USD)': 450.00,
  }, {
    'Speaker': 'Selah Audio RC3R',
    'Enabled': speaker_enable_SelahAudio_RC3R,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/selah-audio-rc3r-spinorama-zip.48264/',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/selah-audio-rc3r-3-way-speaker-review.11218/',
    'Product URL': 'http://www.selahaudio.com/monitors',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/selah-audio-rc3r-3-way-speaker-review-jpg.48249/',
    'Measurement Date': pd.Timestamp('2020-02-01'),
    'Active': False,
    'Price (Single, USD)': 650.00,
  }, {
    'Speaker': 'Tannoy System 600',
    'Enabled': speaker_enable_Tannoy_System600,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/tannoy-system-600-spinorama-zip.53279/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/tannoy-system-600-speaker-review.11919/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/tannoy-system-600-speaker-review-jpg.53268/',
    'Measurement Date': pd.Timestamp('2020-03-08'),
    'Active': False,
    'Price (Single, USD)': 250.00,  # wild guess
  }, {
    'Speaker': 'Zaph Audio ZA5.2 TM (built by Winkleswizard)',
    'Enabled': speaker_enable_ZaphAudio_ZA52TM_Winkleswizard,
    'Data URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/zaph-audio-za5-zip.54633/',
    'Data License': 'Creative Commons BY-NC-SA 4.0',
    'Review URL': 'https://www.audiosciencereview.com/forum/index.php?threads/zaph-audio-za5-diy-kit-speaker-review.12086/',
    'Product URL': 'https://www.audiosciencereview.com/forum/index.php?threads/zaph-audio-za5-2-tm-build-progress.11426/',
    'Picture URL': 'https://www.audiosciencereview.com/forum/index.php?attachments/zaph-audio-za5-diy-speaker-kit-audio-review-jpg.54611/',
    'Measurement Date': pd.Timestamp('2020-03-16'),
    'Active': False,
    'Price (Single, USD)': 170.00,
  },
]).set_index('Speaker')

speakers.loc[:, ['Enabled', 'Active', 'Price (Single, USD)', 'Measurement Date']]

Enabled  Active  \
Speaker                                                         
Adam Audio S2V                                  False    True   
Ascend Acoustics CBM-170 SE                     False   False   
Ascend Acoustics CMT-340 SE Center              False   False   
Ascend Acoustics Sierra-2                       False   False   
Dayton Audio B652-AIR                           False   False   
Elac Adante AS-61                               False   False   
Emotiva Airmotiv 6s                             False    True   
Genelec 8341A                                   False    True   
Harbeth Monitor 30 (low order)                  False   False   
Harbeth Monitor 30 (high order)                 False   False   
JBL 305P MkII                                   False    True   
JBL 705P (sample 1)                             False    True   
JBL 705P (sample 2)                             False    True   
JBL Control 1 Pro                               False    True   
JBL One Series 104                              False    True   
Kali Audio IN-8                                 False    True   
KEF LS50                                        False   False   
KEF Q100                                        False   False   
KEF R3                                          False   False   
Klipsch R-41M                                   False   False   
Klipsch RP-600M                                  True   False   
Micca RB42                                      False   False   
Neumann KH 80 DSP (sample 1)                    False    True   
Neumann KH 80 DSP (sample 2)                    False    True   
Pioneer SP-BS22-LR                              False   False   
Polk T15                                        False   False   
Realistic MC-1000                               False   False   
Revel C52                                       False   False   
Revel F35                                        True   False   
Revel M16                                       False   False   
Selah Audio RC3R                                False   False   
Tannoy System 600                               False   False   
Zaph Audio ZA5.2 TM (built by Winkleswizard)     True   False   

                                              Price (Single, USD)  \
Speaker                                                             
Adam Audio S2V                                              875.0   
Ascend Acoustics CBM-170 SE                                 150.0   
Ascend Acoustics CMT-340 SE Center                          150.0   
Ascend Acoustics Sierra-2                                   740.0   
Dayton Audio B652-AIR                                        39.0   
Elac Adante AS-61                                          1250.0   
Emotiva Airmotiv 6s                                         250.0   
Genelec 8341A                                              2950.0   
Harbeth Monitor 30 (low order)                             1600.0   
Harbeth Monitor 30 (high order)                            1600.0   
JBL 305P MkII                                               150.0   
JBL 705P (sample 1)                                        1000.0   
JBL 705P (sample 2)                                        1000.0   
JBL Control 1 Pro                                            82.0   
JBL One Series 104                                           65.0   
Kali Audio IN-8                                             400.0   
KEF LS50                                                    750.0   
KEF Q100                                                    225.0   
KEF R3                                                     1000.0   
Klipsch R-41M                                                75.0   
Klipsch RP-600M                                             315.0   
Micca RB42                                                   75.0   
Neumann KH 80 DSP (sample 1)                                500.0   
Neumann KH 80 DSP (sample 2)                 

In [3]:
#@markdown
def speaker_list_html():
    doc, tag, text, line = yattag.Doc().ttl()
    for speaker_name in speakers.index:
        speaker = speakers.loc[speaker_name, :]
        with tag('h2', style='clear: left; padding-top: 20px'):
            text(speaker_name + (' (ENABLED)' if speaker['Enabled'] else ''))
        doc.stag('img', src=speaker['Picture URL'], width=200, style='float: left; margin-right: 20px')
        product_url = speaker['Product URL']
        if not pd.isna(product_url):
            line('a', 'Product page', href=speaker['Product URL'], target='_blank')
            text(' - ')
        line('a', 'Review', href=speaker['Review URL'], target='_blank')
        text(' - ')
        line('a', 'Data package', href=speaker['Data URL'], target='_blank')
        doc.stag('br')
        with tag('b'): text('Active' if speaker['Active'] else 'Passive')
        doc.stag('br')
        with tag('b'): text('Price: ')
        text('${:.0f} (single)'.format(speaker['Price (Single, USD)']))
    return doc.getvalue()

IPython.display.HTML(speaker_list_html())

# Data intake

## Download and unpack

This downloads and unpacks speaker measurement data for each *enabled* speaker using the URL specified in `data_url`. This step is skipped if the files already exist in the `speaker_data` folder.

In [4]:
#@markdown
Path('speaker_data').mkdir(exist_ok=True)
for speaker_name, speaker_data_url in speakers.loc[speakers['Enabled'], 'Data URL'].items():
    if not (Path('speaker_data') / speaker_name).exists():
        if not (Path('speaker_data') / (speaker_name + '.zip')).exists():
            !wget -O "speaker_data/{speaker_name}.zip" "{speaker_data_url}"
        !unzip "speaker_data/{speaker_name}.zip" -d "speaker_data/{speaker_name}"

--2020-03-20 09:28:58--  https://www.audiosciencereview.com/forum/index.php?attachments/klipsch-rp-600m-spinorama-zip.55056/
Resolving www.audiosciencereview.com (www.audiosciencereview.com)... 104.27.182.13, 104.27.183.13, 2606:4700:3037::681b:b60d, ...
Connecting to www.audiosciencereview.com (www.audiosciencereview.com)|104.27.182.13|:443... connected.
HTTP request sent, awaiting response... 

200 OK
Length: 85273 (83K) [application/octet-stream]
Saving to: ‘speaker_data/Klipsch RP-600M.zip’

          speaker_d   0%[                    ]       0  --.-KB/s               

speaker_data/Klipsc 100%[===================>]  83.27K  --.-KB/s    in 0.04s   

2020-03-20 09:28:58 (1.81 MB/s) - ‘speaker_data/Klipsch RP-600M.zip’ saved [85273/85273]



Archive:  speaker_data/Klipsch RP-600M.zip
  inflating: speaker_data/Klipsch RP-600M/CEA2034.txt  
  inflating: speaker_data/Klipsch RP-600M/Directivity Index.txt  
  inflating: speaker_data/Klipsch RP-600M/Early Reflections.txt  
  inflating: speaker_data/Klipsch RP-600M/Estimated In-Room Response.txt  
  inflating: speaker_data/Klipsch RP-600M/Horizontal Reflections.txt  
  inflating: speaker_data/Klipsch RP-600M/LICENSE.txt  
  inflating: speaker_data/Klipsch RP-600M/SPL Horizontal.txt  
  inflating: speaker_data/Klipsch RP-600M/SPL Vertical.txt  
  inflating: speaker_data/Klipsch RP-600M/Vertical Reflections.txt  


--2020-03-20 09:28:58--  https://www.audiosciencereview.com/forum/index.php?attachments/revel-f35-spinorama-zip.54290/
Resolving www.audiosciencereview.com (www.audiosciencereview.com)... 104.27.183.13, 104.27.182.13, 2606:4700:3032::681b:b70d, ...
Connecting to www.audiosciencereview.com (www.audiosciencereview.com)|104.27.183.13|:443... connected.
HTTP request sent, awaiting response... 

...

speaker_data/Revel  100%[===================>]  91.17K  --.-KB/s    in 0.09s   

2020-03-20 09:28:58 (1003 KB/s) - ‘speaker_data/Revel F35.zip’ saved [93360/93360]



Archive:  speaker_data/Revel F35.zip
  inflating: speaker_data/Revel F35/CEA2034.txt  
  inflating: speaker_data/Revel F35/Directivity Index.txt  
  inflating: speaker_data/Revel F35/Early Reflections.txt  
  inflating: speaker_data/Revel F35/Estimated In-Room Response.txt  
  inflating: speaker_data/Revel F35/Horizontal Reflections.txt  
  inflating: speaker_data/Revel F35/SPL Horizontal.txt  
  inflating: speaker_data/Revel F35/SPL Vertical.txt  
  inflating: speaker_data/Revel F35/Vertical Reflections.txt  
  inflating: speaker_data/Revel F35/LICENSE.txt  


--2020-03-20 09:28:59--  https://www.audiosciencereview.com/forum/index.php?attachments/zaph-audio-za5-zip.54633/
Resolving www.audiosciencereview.com (www.audiosciencereview.com)... 104.27.183.13, 104.27.182.13, 2606:4700:3032::681b:b70d, ...
Connecting to www.audiosciencereview.com (www.audiosciencereview.com)|104.27.183.13|:443... connected.
HTTP request sent, awaiting response... 

200 OK
Length: 84611 (83K) [application/octet-stream]
Saving to: ‘speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard).zip’

speaker_data/Zaph A 100%[===================>]  82.63K  --.-KB/s    in 0.006s  

2020-03-20 09:28:59 (13.2 MB/s) - ‘speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard).zip’ saved [84611/84611]



Archive:  speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard).zip
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/CEA2034.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/Directivity Index.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/Early Reflections.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/Estimated In-Room Response.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/Horizontal Reflections.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/LICENSE.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/SPL Horizontal.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/SPL Vertical.txt  
  inflating: speaker_data/Zaph Audio ZA5.2 TM (built by Winkleswizard)/Vertical Reflections.txt  


## Load

This loads all data from all speakers into a single, massive `speaker_fr_raw`
DataFrame. The DataFrame index is arranged by speaker name, then frequency. All
data files for each speaker are merged to form the columns of the DataFrame.

In [5]:
#@markdown
# pd.read_table() expects the following multi-level column headers:
#   A, A, A, A, B, B, B, B
#   I, I, J, J, K, K, L, L
#   X, Y, X, Y, X, Y, X, Y
# But the data we have uses the following header format instead:
#   A, B
#   I, J, K, L
#   X, Y, X, Y, X, Y, X, Y
# When confronted with this header, pd.read_table() gets confused and generates
# the following multi-level column index:
#   A, _, _, _, B, _, _, _
#   I, _, J, _, K, _, L, _
#   X, Y, X, Y, X, Y, X, Y
# Where "_" is some autogenerated column name in the form: "Unnamed: 1_level_0"
# This function restores the correct column names by replacing every "Unnamed"
# column with the name of the last known column on that level.
def fix_unnamed_columns(columns):
    last_names = [None] * columns.nlevels
    def fix_column(column):
        for level, label in enumerate(column):
            if not label.startswith('Unnamed: '):
                last_names[level] = label
        return tuple(last_names)
    return pd.MultiIndex.from_tuples(fix_column(column) for column in columns.values)

# Expects input in the following form:
#   (Additional top column levels)
#   FR1                     FR2
#   "Frequency [Hz]" value  "Frequency [Hz]" value
#   42.42            1.234  42.42            2.345
#   43.43            3.456  43.43            5.678
# And reindexes it by the "Frequency [Hz]" column, producing:
#          value
#          (Additional top column labels)
#          FR1    FR2
#   42.42  1.234  2.345
#   43.43  3.456  5.678
def index_by_frequency(data):
    preserve_column_level = list(range(data.columns.nlevels - 1))
    return (data
      # Move all columns levels except the bottommost one into the index
      .stack(level=preserve_column_level)
      # Drop the topmost (default) index level as it's not useful anymore
      .reset_index(level=0, drop=True)
      # Use the frequency as the new bottommost index level
      .set_index('Frequency [Hz]', append=True)
      # Move all other index levels back to columns
      .unstack(level=preserve_column_level))

# In "Sound Pessure Level [dB] / [2.83V 1m]", eliminates " / [2.83V 1m]", as it varies between measurements
def cleanup_spl_column(column):
    match = re.match(r'^(Sound Pessure Level \[dB\])', column)
    return column if match is None else match.group(1)

def load_fr(file):
    fr = pd.read_table(file, header=[0, 1, 2], thousands=',')
    fr.columns = fix_unnamed_columns(fr.columns)
    return (fr
      .rename(columns=cleanup_spl_column)
      .pipe(index_by_frequency))

# If the none_missing() assertion fires, it likely means something is wrong or
# corrupted in the data files of the speaker (e.g. some frequencies present in
# some columns/files but not others)
@ed.none_missing()
def load_speaker(dir):
    return pd.concat(
        (load_fr(file) for file in filter(lambda path: not path.name in ('LICENSE.txt', 'Read License Agreement.txt'), dir.iterdir())),
        axis='columns')

speakers_fr_raw = pd.concat(
  {speaker.Index: load_speaker(Path('speaker_data') / speaker.Index) for speaker in speakers[speakers['Enabled']].itertuples()},
  names=['Speaker'], axis='rows')
speakers_fr_raw

Sound Pessure Level [dB]  \
                                                            Estimated In-Room Response   
                                                            Estimated In-Room Response   
Speaker                                      Frequency [Hz]                              
Klipsch RP-600M                              20.5078                           58.7302   
                                             23.4375                           61.9932   
                                             26.3672                           65.5595   
                                             29.2969                           68.9662   
                                             32.2266                           72.5381   
...                                                                                ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 17753.9000                        70.2127   
                                             18377.9000                        68.4886   
                                             19028.3000                        67.1266   
                                             19699.2000                        66.0925   
                                             19998.0000                        65.6414   

                                                                            \
                                                            SPL Horizontal   
                                                                     -100°   
Speaker                                      Frequency [Hz]                  
Klipsch RP-600M                              20.5078               58.2020   
                                             23.4375               62.0656   
                                             26.3672               65.7788   
                                             29.2969               69.2959   
                                             32.2266               72.9409   
...                                                                    ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 17753.9000            43.5558   
                                             18377.9000            45.7245   
                                             19028.3000            48.7422   
                                             19699.2000            51.0559   
                                             19998.0000            52.1946   

                                                                               \
                                                                                
                                                                -10°    -110°   
Speaker                                      Frequency [Hz]                     
Klipsch RP-600M                              20.5078         57.2313  59.3205   
                                             23.4375         59.5039  63.2204   
                                             26.3672         63.2702  66.7715   
                                             29.2969         66.8984  70.1537   
                                             32.2266         70.6999  73.6666   
...                                                              ...      ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 17753.9000      77.2070  33.5445   
                                             18377.9000      75.8935  35.0396   
                                             19028.3000      75.0654  31.3170   
                                             19699.2000      74.4203  19.0066   
                                             19998.0000      73.9836  28.3247   

                                                                               \
                                                                                
                                                               -120°    -130°   
Speaker                                      Frequency [Hz]                     



# Raw data summary

Basic information about loaded data, including frequency bounds and resolution.


In [6]:
#@markdown
speakers_frequencies = (speakers_fr_raw
  .index
  .to_frame()
  .reset_index(drop=True)
  .groupby('Speaker'))
speakers_frequency_count = speakers_frequencies.count().loc[:, 'Frequency [Hz]'].rename('Frequencies')
speakers_min_frequency = speakers_frequencies.min().loc[:, 'Frequency [Hz]'].rename('Min Frequency (Hz)')
speakers_max_frequency = speakers_frequencies.max().loc[:, 'Frequency [Hz]'].rename('Max Frequency (Hz)')
speakers_octaves = (speakers_max_frequency / speakers_min_frequency).apply(np.log2).rename('Extent (octaves)')
speakers_freqs_per_octave = (speakers_frequency_count / speakers_octaves).rename('Resolution (freqs/octave)')
pd.concat([
  speakers_frequency_count,
  speakers_min_frequency,
  speakers_max_frequency,
  speakers_octaves,
  speakers_freqs_per_octave
], axis='columns')

Frequencies  Min Frequency (Hz)  \
Speaker                                                                         
Klipsch RP-600M                                       181             20.5078   
Revel F35                                             200             20.5078   
Zaph Audio ZA5.2 TM (built by Winkleswizard)          181             20.5078   

                                              Max Frequency (Hz)  \
Speaker                                                            
Klipsch RP-600M                                          19998.0   
Revel F35                                                19999.5   
Zaph Audio ZA5.2 TM (built by Winkleswizard)             19998.0   

                                              Extent (octaves)  \
Speaker                                                          
Klipsch RP-600M                                       9.929467   
Revel F35                                             9.929575   
Zaph Audio ZA5.2 TM (built by Winkleswizard)          9.929467   

                                              Resolution (freqs/octave)  
Speaker                                                                  
Klipsch RP-600M                                               18.228571  
Revel F35                                                     20.141848  
Zaph Audio ZA5.2 TM (built by Winkleswizard)                  18.228571

In [7]:
#@markdown
# Similar to joining `df` against `labels`, but columns from `labels` are added as index levels to `df`, instead of columns.
# Particularly useful when touching columns risks wreaking havoc in a multi-level column index.
#
# For example, given `df`:
#   C0
# A
# i  1 
#    2
# j  3
#    4
#
# And `labels`:
#   C1 C2
# A
# i 1i 2i
# j 1j 2j
#
# Then the result will be:
#         C0
# A C1 C2
# i 1i 2i  1
#          2
# j 1j 2j  3
#          4
def join_index(df, labels):
    return df.align(labels.set_index(list(labels.columns.values), append=True), axis='index')[0]

speakers_fr_annotated = (speakers_fr_raw
    .unstack(level='Frequency [Hz]')
    .pipe(join_index, speakers_freqs_per_octave.to_frame())
    .stack()
)


# Sensitivity

This calculates a single sensitivity value for each speaker using the **mean on-axis SPL** in a configurable frequency band. The result can then be used as the basis for normalization (see next section).


The recommended frequency band is **200-400 Hz**, as it appears to be the most appropriate for normalization - c.f. [Olive](http://www.aes.org/e-lib/online/browse.cfm?elib=12847) (section 3.2.1):

> The use of a reference band of 200-400 Hz is based
> on an observation made in Part One (see section 4.8
> of Part 1). When asked to judge the spectral balance of
> each loudspeaker across 6 frequency bands, listeners
> referenced or anchored their judgments to the band
> centered around 200 Hz. One plausible explanation is
> that many of the fundamentals of instruments,
> including voice, fall within 200-400 Hz, and the
> levels of the higher harmonics are referenced to it.

Note that in other contexts a band centered around 1 kHz is often used.

**CAUTION:** take the numbers in the below table with a grain of salt. Indeed the raw measurement data is using the wrong absolute scale for some speakers, especially active ones.

In [8]:
#@markdown
sensitivity_first_frequency_hz = 200  # @param
sensitivity_last_frequency_hz = 400  # @param

sensitivity_input_column = ('Sound Pessure Level [dB]', 'CEA2034', 'On Axis')
speakers_sensitivity = (speakers_fr_raw
  .loc[speakers_fr_raw.index.to_frame()['Frequency [Hz]'].between(sensitivity_first_frequency_hz, sensitivity_last_frequency_hz), sensitivity_input_column]
  .mean(level='Speaker'))
speakers_sensitivity.to_frame()

Sound Pessure Level [dB]
                                                              CEA2034
                                                              On Axis
Speaker                                                              
Klipsch RP-600M                                             88.197890
Revel F35                                                   89.818955
Zaph Audio ZA5.2 TM (built by Winkleswizard)                83.059010


# Normalization & detrending

This step normalizes *all* SPL frequency response data (on-axis, spinorama, off-axis, estimated in-room response, etc.).


The data is normalized according to the `normalization_mode` variable, which can take the following values:

 - **None**: raw absolute SPL values are carried over as-is.
 - **Equal sensitivity** (recommended): sensitivity values calculated in the previous section are subtracted from all SPL values of each speaker, such that all speakers have 0 dB sensitivity. Improves readability and makes it easier to compare speakers.
 - **Flat on-axis**: the on-axis SPL value is subtracted to itself as well as every other SPL variable at each frequency. In other words this simulates EQ'ing every speaker to be perfectly flat on-axis. Use this mode to focus solely on directivity data.
 - **Flat listening window**: same as above, using the Listening Window average instead of On-Axis.
 - **Detrend**: for each speaker, computes a smoothed response (using the same mechanism as described in the *Smoothing* section below), then subtracts it from the original responses. In other words, this is the opposite of smoothing. Useful for removing trends (e.g. overall bass/treble balance) to focus solely on local variations.

In [9]:
#@markdown
normalization_mode = 'Equal sensitivity'  # @param ["None", "Equal sensitivity", "Flat on-axis", "Flat listening window", "Detrend"]
#@markdown ## Detrending settings
#@markdown These settings only have an effect if `normalization_mode` is set to "Detrend".
#@markdown
#@markdown A smoothed version of the selected response will be subtracted to all responses for that speaker, *excluding* directivity indices.
#@markdown If *Detrend each response individually* is selected, individual responses are smoothed and subtracted independently of each other, *including* directivity indices.
detrend_reference = 'On Axis'  # @param ["On Axis", "Listening Window", "Early Reflections", "Sound Power", "Detrend each response individually"]
#@markdown Select the smoothing strength. You can also input a custom value as long as you follow the same pattern, e.g. `1/10-octave`.
detrend_octaves = '1/1-octave'  # @param {allow-input: true} ["2/1-octave", "1/1-octave", "1/2-octave", "1/3-octave", "1/6-octave"]

detrend_octaves_match = re.search('(\d+)/(\d+)', detrend_octaves)
detrend_octaves_number = float(detrend_octaves_match.group(1))/float(detrend_octaves_match.group(2))

def smooth(speaker_fr, octaves):
    (freqs_per_octave,) = speaker_fr.index.to_frame().loc[:, 'Resolution (freqs/octave)'].unique()
    return (speaker_fr
        # Ensure the input to ewm() is sorted by frequency, otherwise things will get weird fast. This should already be the case, but make sure regardless.
        .sort_index()
        # Note that this assumes points are equally spaced in log-frequency. This assumption holds for all our current datasets.
        .ewm(span=freqs_per_octave*octaves).mean()
    )

speakers_fr_splnorm = speakers_fr_annotated.loc[:, 'Sound Pessure Level [dB]']
speakers_fr_dinorm = speakers_fr_annotated.loc[:, '[dB] Directivity Index ']
spl_axis_label = ['Absolute Sound Pressure Level (dB SPL)']
di_axis_label = ['Directivity Index (dBr)']
spl_domain = (55, 105)
di_domain = (-5, 10)
if normalization_mode == 'Equal sensitivity':
    speakers_fr_splnorm = speakers_fr_splnorm.sub(
        speakers_sensitivity, axis='index', level='Speaker')
    spl_axis_label = ['Relative Sound Pressure (dBr)']
    spl_domain = (-40, 10)
if normalization_mode == 'Flat on-axis':
    speakers_fr_splnorm = speakers_fr_splnorm.sub(
        speakers_fr_raw.loc[:, ('Sound Pessure Level [dB]', 'CEA2034', 'On Axis')], axis='index')
    spl_axis_label = ['Sound Pressure (dBr)', 'relative to on-axis']
    spl_domain = (-40, 10)
if normalization_mode == 'Flat listening window':
    speakers_fr_splnorm = speakers_fr_splnorm.sub(
        speakers_fr_raw.loc[:, ('Sound Pessure Level [dB]', 'CEA2034', 'Listening Window')], axis='index')
    spl_axis_label = ['Sound Pressure (dBr)', 'relative to listening window']
    spl_domain = (-40, 10)
if normalization_mode == 'Detrend':
    if detrend_reference == 'Detrend each response individually':
        speakers_fr_splnorm = speakers_fr_splnorm.sub(speakers_fr_splnorm
            .groupby('Speaker')
            .apply(smooth, detrend_octaves_number))
        spl_axis_label = ['Sound Pressure (dBr)', '{} detrended'.format(detrend_octaves)]
        spl_domain = (-25, 25)
        speakers_fr_dinorm = speakers_fr_dinorm.sub(speakers_fr_dinorm
            .groupby('Speaker')
            .apply(smooth, detrend_octaves_number))
        di_axis_label = ['Directivity Index (dBr)', '{} detrended'.format(detrend_octaves)]
        di_domain = (-7.5, 7.5)
    else:
        speakers_fr_splnorm = speakers_fr_splnorm.sub(speakers_fr_splnorm.loc[:, ('CEA2034', detrend_reference)]
            .groupby('Speaker')                     
            .apply(smooth, detrend_octaves_number), axis='index')
        spl_axis_label = ['Sound Pressure (dBr)', 'relative to {} smoothed {} (dBr)'.format(detrend_octaves, detrend_reference)]
        spl_domain = (-40, 10)
        
speakers_fr_norm = pd.concat([speakers_fr_splnorm, speakers_fr_dinorm], axis='columns')
speakers_fr_norm

CEA2034  \
                                                                                      DI offset   
Speaker                                      Resolution (freqs/octave) Frequency [Hz]             
Klipsch RP-600M                              18.228571                 20.5078        -38.21849   
                                                                       23.4375        -38.21849   
                                                                       26.3672        -38.21849   
                                                                       29.2969        -38.21849   
                                                                       32.2266        -38.21849   
...                                                                                         ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 18.228571                 17753.9000     -43.07961   
                                                                       18377.9000     -43.07961   
                                                                       19028.3000     -43.07961   
                                                                       19699.2000     -43.07961   
                                                                       19998.0000     -43.07961   

                                                                                                         \
                                                                                      Early Reflections   
Speaker                                      Resolution (freqs/octave) Frequency [Hz]                     
Klipsch RP-600M                              18.228571                 20.5078                -30.55969   
                                                                       23.4375                -27.59299   
                                                                       26.3672                -23.84559   
                                                                       29.2969                -20.28329   
                                                                       32.2266                -16.55049   
...                                                                                                 ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 18.228571                 17753.9000             -12.56561   
                                                                       18377.9000             -14.38601   
                                                                       19028.3000             -15.78871   
                                                                       19699.2000             -16.81451   
                                                                       19998.0000             -17.25211   

                                                                                                            \
                                                                                      Early Reflections DI   
Speaker                                      Resolution (freqs/octave) Frequency [Hz]                        
Klipsch RP-600M                              18.228571                 20.5078                   -38.75669   
                                                                       23.4375                   -39.42699   
                                                                       26.3672                   -39.35209   
                                                                       29.2969                   -39.25959   
                                                                       32.2266                   -39.16069   
...                                                                                                    ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 18.228571                 17753.9000                -38.05091   
                                                                       18377.9000                -37.7


# Smoothing

All responses (including directivity indices) are smoothed according to the settings below.


Smoothing is done by applying an [exponential moving average (EMA)](https://en.wikipedia.org/wiki/Moving_average#Exponential_moving_average) with a "span" or "N" corresponding to the number of octaves chosen (since points in the input are already equally spaced in log-frequency). EMA was chosen over a simple moving average because it gracefully handles the case where N is not an integer, as is often the case here.

In [10]:
#@markdown
#@markdown Select the smoothing strength. You can also input a custom value as long as you follow the same pattern, e.g. `1/10-octave smoothing`.
smoothing_mode = 'No smoothing'  # @param {allow-input: true} ["1/1-octave smoothing", "1/2-octave smoothing", "1/3-octave smoothing", "1/6-octave smoothing", "1/12-octave smoothing", "No smoothing"]
#@markdown If this is checked, smoothed data is displayed alongside the original, unsmoothed data. Otherwise, the unsmoothed data is dropped.
smoothing_preserve_original = True  # @param {type:"boolean"}

smoothing_mode_match = re.search('(\d+)/(\d+)', smoothing_mode)
smoothing_octaves = float(smoothing_mode_match.group(1))/float(smoothing_mode_match.group(2)) if smoothing_mode_match else None

# Appends a new index level with all identical values.
def append_constant_index(df, value, name=None):
    return df.set_index(pd.Index([value] * df.shape[0], name=name), append=True)

speakers_fr_smoothed = (speakers_fr_norm
    .unstack(level='Frequency [Hz]')
    .pipe(append_constant_index, 'No smoothing', name='Smoothing')
    .stack()
)
if smoothing_octaves is not None:
    speakers_fr_smoothed_only = (speakers_fr_norm
        .groupby('Speaker')
        .apply(smooth, smoothing_octaves)
        .pipe(append_constant_index, smoothing_mode, name='Smoothing'))
    speakers_fr_smoothed = (
        pd.concat([speakers_fr_smoothed, speakers_fr_smoothed_only])
        if smoothing_preserve_original else speakers_fr_smoothed_only)
speakers_fr_smoothed

CEA2034  \
                                                                                                   DI offset   
Speaker                                      Resolution (freqs/octave) Smoothing    Frequency [Hz]             
Klipsch RP-600M                              18.228571                 No smoothing 20.5078        -38.21849   
                                                                                    23.4375        -38.21849   
                                                                                    26.3672        -38.21849   
                                                                                    29.2969        -38.21849   
                                                                                    32.2266        -38.21849   
...                                                                                                      ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 18.228571                 No smoothing 17753.9000     -43.07961   
                                                                                    18377.9000     -43.07961   
                                                                                    19028.3000     -43.07961   
                                                                                    19699.2000     -43.07961   
                                                                                    19998.0000     -43.07961   

                                                                                                                      \
                                                                                                   Early Reflections   
Speaker                                      Resolution (freqs/octave) Smoothing    Frequency [Hz]                     
Klipsch RP-600M                              18.228571                 No smoothing 20.5078                -30.55969   
                                                                                    23.4375                -27.59299   
                                                                                    26.3672                -23.84559   
                                                                                    29.2969                -20.28329   
                                                                                    32.2266                -16.55049   
...                                                                                                              ...   
Zaph Audio ZA5.2 TM (built by Winkleswizard) 18.228571                 No smoothing 17753.9000             -12.56561   
                                                                                    18377.9000             -14.38601   
                                                                                    19028.3000             -15.78871   
                                                                                    19699.2000             -16.81451   
                                                                                    19998.0000             -17.25211   

                                                                                                                         \
                                                                                                   Early Reflections DI   
Speaker                                      Resolution (freqs/octave) Smoothing    Frequency [Hz]                        
Klipsch RP-600M                              18.228571                 No smoothing 20.5078                   -38.75669   
                                                                                    23.4375                   -39.42699   
                                                                                    26.3672                   -39.35209   
                                                                                    29.2969                   -39


# Plot settings

Here you can customize some parameters related to the charts.


In [11]:
#@markdown
# @markdown Dimensions for standalone charts
standalone_chart_width = 800  # @param {type:"integer"}
standalone_chart_height = 400  # @param {type:"integer"}
# @markdown Dimensions for side-by-side charts
sidebyside_chart_width = 600  # @param {type:"integer"}
sidebyside_chart_height = 300  # @param {type:"integer"}

# Removes index levels from `df` that have identical values throughout.
# Also returns a Series with the index levels that were removed, along with their common value.
#
# For example, given:
#          COL
#  A  B  C
# a1  b  c   1
# a2  b  c   2
# a2  b  c   3
#
# Will return:
#    COL
#  A
# a1   1
# a2   2
# a2   3
#
# And:
# B b
# C c
def extract_common_index_levels(df):
    index_df = (df
        .index
        .to_frame()
        .reset_index(drop=True)
    )
    index_has_distinct_values = index_df.nunique() > 1
    index_common_names = index_has_distinct_values.loc[~index_has_distinct_values].index
    def extract_unique_index_value(index_name):
        (unique_index_value,) = index_df.loc[:, index_name].unique()
        return unique_index_value
    common_info = (index_common_names
        .to_series()
        .apply(extract_unique_index_value)
    )
    df = df.copy()
    df.index = pd.MultiIndex.from_frame(
        index_df.drop(columns=index_common_names))
    return df, common_info

# Rearranges the index, folding metadata such as resolution and smoothing into the "Speaker" index level.
def fold_speakers_info(speakers_fr):
    speakers_fr = (speakers_fr
        .unstack(level='Frequency [Hz]')
        .copy()
    )
    speakers_fr.index = pd.MultiIndex.from_frame(speakers_fr
        .index
        .to_frame()
        .apply(
            # Ideally this should be on multiple lines, but it's not clear if that's feasible: https://github.com/vega/vega-lite/issues/5994
            lambda speaker: pd.Series({'Speaker': '; '.join(speaker)}),
            axis='columns')
    )
    return speakers_fr.stack()

(speakers_fr_ready, common_title) = (speakers_fr_smoothed
    .rename(
        level='Resolution (freqs/octave)',
        index=lambda freqs_per_octave: '{:.2g} pts/octave'.format(freqs_per_octave))
    .rename_axis(index={'Resolution (freqs/octave)': 'Resolution'})
    .pipe(extract_common_index_levels)
)
single_speaker_mode = speakers_fr_ready.index.names == ['Frequency [Hz]']
if single_speaker_mode:
    # Re-add an empty Speaker index level.
    # The alternative would be to handle this case specially in every single graph, which gets annoying fast.
    speakers_fr_ready = (speakers_fr_ready
        .pipe(append_constant_index, '', name='Speaker')
        .swaplevel(0, -1)
    )
else:
    speakers_fr_ready = fold_speakers_info(speakers_fr_ready)
common_title = alt.TitleParams(
    text='; '.join(common_title.to_list()),
    anchor='start')

speakers_license = speakers.loc[
    speakers_fr_smoothed.index.get_level_values('Speaker').drop_duplicates(),
    'Data License']
credits = ['Data: amirm, AudioScienceReview.com - Plotted by Loudspeaker Explorer']
if speakers_license.nunique(dropna=False) == 1:
    (unique_license,) = speakers_license.unique()
    if (pd.notna(unique_license)):
        credits.append('Data licensed under {}'.format(unique_license))
else:
    for speaker, license in speakers_license.dropna().items():
        credits.append('{} data licensed under {}'.format(speaker, license))

alt.data_transformers.disable_max_rows()

# Prepares DataFrame `df` for charting using alt.Chart().
#
# Altair doesn't use the index, so we move it into columns. Then columns are
# renamed according to the `columns_mapper` dict. (This is necessary because
# Altair doesn't work well with verbose column names, and it doesn't support
# multi-level columns anyway.) Columns that don't appear in the dict are
# dropped.
#
# Note: contrary to DataFrame.rename(), in the case of MultiIndex columns,
# `columns_mapper` keys are matched against the full column name (i.e. a tuple),
# not individual per-level labels.
def prepare_alt_chart(df, columns_mapper):
    df = df.reset_index().loc[:, list(columns_mapper.keys())]
    df.columns = df.columns.map(mapper=columns_mapper)
    return df

def frequency_response_chart(data, sidebyside=False, additional_tooltips=[]):
    if single_speaker_mode:
        sidebyside = False
    return (alt.Chart(data, title=common_title)
      .properties(
        width=sidebyside_chart_width if sidebyside else standalone_chart_width,
        height=sidebyside_chart_height if sidebyside else standalone_chart_height)
      .encode(
          frequency_xaxis('frequency'),
          tooltip=additional_tooltips + [
              alt.Tooltip('frequency', title='Frequency (Hz)', format='.03s'),
              alt.Tooltip('value', title='Value (dB)', format='.2f')]))

# This is equivalent to using the `point` line mark property.
# The reason why we don't simply do that tooltips wouldn't work as well due to this Vega-lite bug: https://github.com/vega/vega-lite/issues/6107
def mark_line_with_points(chart):
    mouseover = alt.selection_single(on='mouseover', empty='none')
    return alt.layer(
        chart
            .mark_circle(clip=True, size=100)
            .add_selection(mouseover)
            .encode(fillOpacity=alt.condition(mouseover, alt.value(0.3), alt.value(0)))
            .interactive(),
        chart.mark_line(clip=True, interpolate='monotone')
    )

def frequency_xaxis(shorthand):
    return alt.X(shorthand, title='Frequency (Hz)', scale=alt.Scale(type='log', base=10, nice=False), axis=alt.Axis(format='s'))

def sound_pressure_yaxis(title_prefix=None):
    return alt.Y('value', title=[(title_prefix + ' ' if title_prefix else '') + spl_axis_label[0]] + spl_axis_label[1:], scale=alt.Scale(domain=spl_domain), axis=alt.Axis(grid=True))

def directivity_index_yaxis(title_prefix=None, scale_domain=di_domain):
    return alt.Y('value', title=[(title_prefix + ' ' if title_prefix else '') + di_axis_label[0]] + di_axis_label[1:], scale=alt.Scale(domain=scale_domain), axis=alt.Axis(grid=True))

def variable_color(*kargs, **kwargs):
     return alt.Color('variable', title=None, sort=None, legend=alt.Legend(symbolType='stroke'), *kargs, **kwargs)

def speaker_color():
    # Configure the legend so that it shows long labels correctly. This is necessary because of the resolution/smoothing/etc. metadata.
    return alt.Color(
        'speaker',
        title=None,
        legend=None if single_speaker_mode else alt.Legend(orient='top', direction='vertical', labelLimit=600, symbolType='stroke'))

def interactive_legend(chart, encoding_channel):
    selection = alt.selection_multi(fields=[encoding_channel.shorthand], bind='legend')
    return (chart
        .add_selection(selection)
        .encode(
            encoding_channel,
            opacity=alt.condition(selection, alt.value(1), alt.value(0.2)))
    )

# Given a DataFrame with some of the columns in the following format:
#   'On-Axis' '10°' '20°' '-10°' ...
# Converts the above column labels to the following:
#   0.0 10.0 20.0 -10.0
def convert_angles(df):
    def convert_label(label):
        if label == 'On-Axis':
            return 0.0
        stripped_label = label.strip('°')
        if stripped_label == label:
            return label
        try:
            return float(stripped_label)
        except ValueError:
            return label
    return df.rename(columns=convert_label)

def postprocess_chart(chart):
    # Altair/Vega-Lite doesn't provide a way to set multiple titles or just display arbitrary text.
    # We hack around that limitation by concatenating with a dummy chart that has a title.
    # See https://github.com/vega/vega-lite/issues/5997
    return (alt.vconcat(
        chart,
        alt.Chart(title=alt.TitleParams(
            credits, fontSize=10, fontWeight='lighter', color='gray', anchor='start')).mark_text())
        .resolve_legend(color='independent')
        .configure_view(width=600, height=1, opacity=0))

# Standard measurements

Note that all the data shown in this section is a direct representation of the input data after normalization. No complex processing is done. In particular, data for derived metrics such as *Listening Window*, *Early Reflections*, *Sound Power*, Directivity Indices and even *Estimated In-Room Response* come directly from the input - they are not derived by this code.

## Spinorama

The famous CEA/CTA-2034 charts, popularized by Dr. Floyd Toole. These provide a good summary of the measurements from a perceptual perspective. Speakers are presented side-by-side for easy comparison.

Remember:
 - **All the charts are interactive.** Use the mousewheel to zoom, and drag & drop to pan. Click on a legend entry to highlight a single response; hold shift to highlight multiple responses. Double-click to reset the view.
 - **Charts will not be generated if the section they're under is folded while the notebook is running.** To manually load a chart after running the notebook, click on the square to the left of the *Show Code* button. Or simply use *Run all* again after unfolding the section.

In [12]:
#@markdown
spinorama_chart_legend_selection = alt.selection_multi(fields=['variable'], bind='legend')
spinorama_chart_common = alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('CEA2034', 'On Axis'): 'On Axis',
          ('CEA2034', 'Listening Window'): 'Listening Window',
          ('CEA2034', 'Early Reflections'): 'Early Reflections',
          ('CEA2034', 'Sound Power'): 'Sound Power',
          ('Directivity Index', 'Early Reflections DI'): 'Early Reflections DI',
          ('Directivity Index', 'Sound Power DI'): 'Sound Power DI',
        }).melt(['speaker', 'frequency']),
    lambda data: frequency_response_chart(data,
        sidebyside=True,
        additional_tooltips=[alt.Tooltip('variable', title='Response')]))

# Note that there are few subtleties here because of Altair/Vega quirks:
# - To make the Y axes independent, `.resolve_scale()` has to be used *before
#   and after* `.facet()`. (In Vega terms, there needs to be a Resolve property
#   in *every* view composition specification.)
#   - If the first `.resolve_scale()` is removed from the layer spec, the axes
#     are not made independent.
#   - If the second `.resolve_scale()` is removed from the facet spec, Vega
#     throws a weird `Unrecognized scale name: "child_layer_0_y"` error.
# - To make the two axes zoom and pan at the same time, `.interactive()` has to
#   be used on each encoding, not on the overall view. Otherwise only the left
#   axis will support zoom & pan.
alt.pipe(
    alt.layer(
        alt.pipe(
            spinorama_chart_common
                .encode(sound_pressure_yaxis())
                .transform_filter(alt.FieldOneOfPredicate(field='variable', oneOf=['On Axis', 'Listening Window', 'Early Reflections', 'Sound Power'])),
            mark_line_with_points),
        alt.pipe(
            spinorama_chart_common
                .encode(directivity_index_yaxis(scale_domain=(-10, 40)))
                .transform_filter(alt.FieldOneOfPredicate(field='variable', oneOf=['Early Reflections DI', 'Sound Power DI'])),
            mark_line_with_points))
        .resolve_scale(y='independent'),
    lambda chart: interactive_legend(chart, variable_color())
        .facet(alt.Column('speaker', title=None), title=common_title)
        .resolve_scale(y='independent'),
    postprocess_chart)

alt.VConcatChart(...)

## On-axis response

In [13]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
            ('Speaker', ''): 'speaker',
            ('Frequency [Hz]', ''): 'frequency',
            ('CEA2034', 'On Axis'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(sound_pressure_yaxis(title_prefix='On Axis')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)


## Off-axis responses

Note that this chart can be particularly taxing on your browser due to the sheer number of points.


Use the slider at the bottom to focus on a specific angle. Note that the slider can be slow to respond, especially if there are many speakers. Double-click the chart to reset.

Keep in mind that these graphs can be shown normalized to flat on-axis by changing the settings in the *Normalization* section above.

In [14]:
#@markdown
off_axis_angle_selection = alt.selection_single(
    fields=['angle'],
    bind=alt.binding_range(min=-170, max=180, step=10, name='Angle selector (°)'),
    clear='dblclick')
alt.pipe(
    speakers_fr_ready
        .loc[:, ['SPL Horizontal', 'SPL Vertical']]
        .pipe(convert_angles)
        .rename_axis(columns=['Direction', 'Angle'])
        .rename(columns={'SPL Horizontal': 'Horizontal', 'SPL Vertical': 'Vertical'}, level='Direction')
        .stack(level=['Direction', 'Angle'])
        .reset_index()
        .pipe(prepare_alt_chart, {
            'Speaker': 'speaker',
            'Direction': 'direction',
            'Angle': 'angle',
            'Frequency [Hz]': 'frequency',
            0: 'value',
          }),
    lambda data: frequency_response_chart(data,
        sidebyside=True,
        additional_tooltips=[alt.Tooltip('angle', title='Angle (°)')])
        .transform_filter(off_axis_angle_selection)
        .encode(
            alt.Color(
              'angle', title='Angle (°)',
              scale=alt.Scale(scheme='sinebow', domain=(-180, 180)),
              legend=alt.Legend(gradientLength=600, values=list(range(-180, 180+10, 10)))),
            sound_pressure_yaxis()),
    mark_line_with_points,
    lambda chart: chart
        .add_selection(off_axis_angle_selection)
        .facet(
            column=alt.Column('speaker', title=None),
            row=alt.Row('direction', title=None)),
    postprocess_chart)

alt.VConcatChart(...)


## Horizontal reflection responses


In [15]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .loc[:, 'Horizontal Reflections']
        .rename_axis(columns=['Direction'])
        .rename(columns=lambda column: re.sub(' ?Horizontal ?', '', re.sub(' ?Reflection ?', '', column)))
        .stack(level=['Direction'])
        .reset_index()
        .pipe(prepare_alt_chart, {
            'Speaker': 'speaker',
            'Direction': 'variable',
            'Frequency [Hz]': 'frequency',
            0: 'value',
        }),
    lambda data: frequency_response_chart(data,
        sidebyside=True,
        additional_tooltips=[alt.Tooltip('variable', title='Direction')])
        .encode(sound_pressure_yaxis()),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, variable_color())
        .facet(alt.Column('speaker', title=None)),
    postprocess_chart)

alt.VConcatChart(...)


## Vertical reflection responses


In [16]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .loc[:, 'Vertical Reflections']
        .rename_axis(columns=['Direction'])
        .rename(columns=lambda column: re.sub(' ?Vertical ?', '', re.sub(' ?Reflection ?', '', column)))
        .stack(level=['Direction'])
        .reset_index()
        .pipe(prepare_alt_chart, {
            'Speaker': 'speaker',
            'Direction': 'variable',
            'Frequency [Hz]': 'frequency',
            0: 'value',
        }),
    lambda data: frequency_response_chart(data,
        sidebyside=True,
        additional_tooltips=[alt.Tooltip('variable', title='Direction')])
        .encode(sound_pressure_yaxis()),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, variable_color())
        .facet(alt.Column('speaker', title=None)),
    postprocess_chart)

alt.VConcatChart(...)

## Listening Window response

In [17]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('CEA2034', 'Listening Window'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(sound_pressure_yaxis(title_prefix='Listening Window')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

## Early Reflections response

In [18]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('CEA2034', 'Early Reflections'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(sound_pressure_yaxis(title_prefix='Early Reflections')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

## Sound Power response

In [19]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('CEA2034', 'Sound Power'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(sound_pressure_yaxis(title_prefix='Sound Power')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

## Early Reflections Directivity Index

In [20]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('Directivity Index', 'Early Reflections DI'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(directivity_index_yaxis(title_prefix='Early Reflections')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

## Sound Power Directivity Index

In [21]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('Directivity Index', 'Sound Power DI'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(directivity_index_yaxis(title_prefix='Sound Power')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

## Estimated In-Room Response

In [22]:
#@markdown
alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
          ('Speaker', ''): 'speaker',
          ('Frequency [Hz]', ''): 'frequency',
          ('Estimated In-Room Response', 'Estimated In-Room Response'): 'value',
        }),
    lambda data: frequency_response_chart(data,
        additional_tooltips=[alt.Tooltip('speaker', title='Speaker')])
        .encode(sound_pressure_yaxis(title_prefix='Estimated In-Room Response')),
    mark_line_with_points,
    lambda chart: interactive_legend(chart, speaker_color()),
    postprocess_chart)

alt.VConcatChart(...)

# Other measurements


## Listening Window detail

The Listening Window is defined by CTA-2034-A as the average of on-axis, ±10° vertical responses, and ±10º, ±20º and ±30º horizontal responses. Averages can be misleading as they can hide significant variation between angles.

This chart provides more detail by including each individual angle that is used in the Listening Window average. This can be used to assess the consistency of the response within the Listening Window.

In [23]:
#@markdown
listening_window_detail_common = alt.pipe(
    speakers_fr_ready
        .pipe(prepare_alt_chart, {
            ('Speaker', ''): 'speaker',
            ('Frequency [Hz]', ''): 'frequency',
            ('CEA2034', 'Listening Window'): 'Listening Window',
            ('CEA2034', 'On Axis'): 'On Axis',
            ('SPL Vertical', '-10°'): '-10° Vertical',
            ('SPL Vertical',  '10°'): '+10° Vertical',
            ('SPL Horizontal', '-10°'): '-10° Horizontal',
            ('SPL Horizontal',  '10°'): '+10° Horizontal',
            ('SPL Horizontal', '-20°'): '-20° Horizontal',
            ('SPL Horizontal',  '20°'): '+20° Horizontal',
            ('SPL Horizontal', '-30°'): '-30° Horizontal',
            ('SPL Horizontal',  '30°'): '+30° Horizontal',
        })
        .melt(['speaker', 'frequency']),
    lambda data: frequency_response_chart(data,
        sidebyside=True,
        additional_tooltips=[alt.Tooltip('variable', title='Response')])
        .encode(sound_pressure_yaxis()))

listening_window_detail_highlight = alt.FieldOneOfPredicate(
    field='variable',
    oneOf=['Listening Window', 'On Axis'])

alt.pipe(
    alt.layer(
        alt.pipe(
            listening_window_detail_common
                .transform_filter({'not': listening_window_detail_highlight})
                .encode(strokeWidth=alt.value(1.5)),
            mark_line_with_points),
        alt.pipe(
            listening_window_detail_common
                .transform_filter(listening_window_detail_highlight),
            mark_line_with_points)),
    lambda chart: interactive_legend(chart,
        variable_color(scale=alt.Scale(
            range=['#aeadd3', '#796db2', '#cec5c1', '#c0b8b4', '#b3aaa7', '#a59c99', '#98908c', '#8b827f', '#ff7f0e', '#2ca02c']
        )))
        .facet(alt.Column('speaker', title=None), title=common_title)
        .interactive(),
    postprocess_chart
)

alt.VConcatChart(...)